## Assignment: Segmentation and Clustering Neighbourhood in Toronto

In [104]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import requests
import numpy as np
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim
import folium
from sklearn.cluster import KMeans
import json
from pandas.io.json import json_normalize

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
print('Libraries Imported')

Libraries Imported


In [105]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
html_data = requests.get(url).text
soup = BeautifulSoup(html_data,'html5lib')

In [106]:
tag_object = soup.ta

In [107]:
table_contents=[]
table=soup.find('table')
table
for row in table.findAll('td'):
    cell = {}
    if row.span.text=='Not assigned':
        pass
    else:
        cell['PostalCode'] = row.p.text[:3]
        cell['Borough'] = (row.span.text).split('(')[0]
        cell['Neighborhood'] = (((((row.span.text).split('(')[1]).strip(')')).replace(' /',',')).replace(')',' ')).strip(' ')
        table_contents.append(cell)


In [108]:
# print(table_contents)
df=pd.DataFrame(table_contents)
df['Borough']=df['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})
df.head()

PostalCode           Borough                      Neighborhood
0        M3A        North York                         Parkwoods
1        M4A        North York                  Victoria Village
2        M5A  Downtown Toronto         Regent Park, Harbourfront
3        M6A        North York  Lawrence Manor, Lawrence Heights
4        M7A      Queen's Park     Ontario Provincial Government

In [109]:
df.shape

(103, 3)

In [110]:
# !conda install -c conda-forge geocoder --yes
import geocoder # import geocoder

In [111]:
lat_lng = pd.read_csv('Geospatial_Coordinates.csv')
lat_lng.rename(columns ={'Postal Code':'PostalCode'}, inplace = True)
lat_lng.head()

# initialize your variable to None
# lat_lng_coords = None
# postal_code = df['PostalCode']
# postal_code
# for  x, pin in postal_code.items():
# # loop until you get the coordinates
#     while(lat_lng_coords is None):
#       g = geocoder.arcgis('{}, Toronto, Ontario'.format(pin))
#       lat_lng_coords = g.latlng
#     # print(pin)
#     latitude = lat_lng_coords[0]
#     longitude = lat_lng_coords[1]
#     lat_lng = lat_lng.append({'Latitude':latitude,'Longitude':longitude}, ignore_index = True)
    
# lat_lng['Latitude'].value_counts()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [112]:

df = df.merge(lat_lng, on = ['PostalCode'],how = 'left')
df.head()

PostalCode           Borough                      Neighborhood   Latitude  \
0        M3A        North York                         Parkwoods  43.753259   
1        M4A        North York                  Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4        M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

### Printing the number of Boroughs and Neighbourhoods

In [113]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 15 boroughs and 103 neighborhoods.


### Using geopy library to get the latitude and longitude values of Toronto

In [114]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="tr_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


### Create a map of Toronto with neighbourhoods superimposed on top

In [115]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define Foursquare Credentials and Version

In [116]:
CLIENT_ID = 'J4I2WAJEINOGGWERVMKOIYECJDP3BL0B23524WTXGX00TYED' # your Foursquare ID
CLIENT_SECRET = 'E5YPAY4DNF2AN1HZ3KUSEJAIHJARRGPJ5T5VGFRT3CDPUNJK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: J4I2WAJEINOGGWERVMKOIYECJDP3BL0B23524WTXGX00TYED
CLIENT_SECRET:E5YPAY4DNF2AN1HZ3KUSEJAIHJARRGPJ5T5VGFRT3CDPUNJK


In [117]:
df.loc[0,'Neighborhood']

'Parkwoods'

### Get the neighbourhood's latitude and longitude

In [118]:
neighborhood_latitude = df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = df.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 1000 meters

### First, let's create the GET request URL. Name your URL url.

In [119]:

LIMIT = 100
radius = 1000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=J4I2WAJEINOGGWERVMKOIYECJDP3BL0B23524WTXGX00TYED&client_secret=E5YPAY4DNF2AN1HZ3KUSEJAIHJARRGPJ5T5VGFRT3CDPUNJK&v=20180605&ll=43.7532586,-79.3296565&radius=1000&limit=100'

In [120]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '60743318c152517b3b20c39a'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 29,
  'suggestedBounds': {'ne': {'lat': 43.762258609000014,
    'lng': -79.31721997969855},
   'sw': {'lat': 43.74425859099999, 'lng': -79.34209302030145}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b8991cbf964a520814232e3',
       'name': "Allwyn's Bakery",
       'location': {'address': '81 Underhill drive',
        'lat': 43.75984035203157,
        'lng': -79.32471879917513,
        'labeledLatLngs': [{'label': 'display'

In [121]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

### Cleaning JSON and converting to dataframe

In [122]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-122-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name            categories        lat        lng
0    Allwyn's Bakery  Caribbean Restaurant  43.759840 -79.324719
1    Brookbanks Park                  Park  43.751976 -79.332140
2        Tim Hortons                  Café  43.760668 -79.326368
3  Bruno's valu-mart         Grocery Store  43.746143 -79.324630
4                A&W  Fast Food Restaurant  43.760643 -79.326865

In [123]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

29 venues were returned by Foursquare.


# Explore neighbourhoods in Toronto

In [124]:
### Get the top 100 venues from each of the neighbourhoods in Toronto

In [125]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [126]:
# type your answer here
toronto_venues = getNearbyVenues(names = df['Neighborhood'],latitudes = df['Latitude'],
                                  longitudes = df['Longitude'])
toronto_venues

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills North
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
The Danforth  East
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview East
The Danforth

Neighborhood  \
0                                             Parkwoods   
1                                             Parkwoods   
2                                             Parkwoods   
3                                             Parkwoods   
4                                             Parkwoods   
5                                             Parkwoods   
6                                             Parkwoods   
7                                             Parkwoods   
8                                             Parkwoods   
9                                             Parkwoods   
10                                            Parkwoods   
11                                            Parkwoods   
12                                            Parkwoods   
13                                            Parkwoods   
14                                            Parkwoods   
15                                            Parkwoods   
16                                            Parkwoods   
17                                            Parkwoods   
18                                            Parkwoods   
19                                            Parkwoods   
20                                            Parkwoods   
21                                            Parkwoods   
22                                            Parkwoods   
23                                            Parkwoods   
24                                            Parkwoods   
25                                            Parkwoods   
26                                            Parkwoods   
27                                            Parkwoods   
28                                            Parkwoods   
29                                     Victoria Village   
30                                     Victoria Village   
31                                     Victoria Village   
32                                     Victoria Village   
33                                     Victoria Village   
34                                     Victoria Village   
35                                     Victoria Village   
36                                     Victoria Village   
37                                     Victoria Village   
38                                     Victoria Village   
39                                     Victoria Village   
40                            Regent Park, Harbourfront   
41                            Regent Park, Harbourfront   
42                            Regent Park, Harbourfront   
43                            Regent Park, Harbourfront   
44                            Regent Park, Harbourfront   
45                            Regent Park, Harbourfront   
46                            Regent Park, Harbourfront   
47                            Regent Park, Harbourfront   
48                            Regent Park, Harbourfront   
49                            Regent Park, Harbourfront   
50                            Regent Park, Harbourfront   
51                            Regent Park, Harbourfront   
52                            Regent Park, Harbourfront   
53                            Regent Park, Harbourfront   
54                            Regent Park, Harbourfront   
55                            Regent Park, Harbourfront   
56                            Regent Park, Harbourfront   
57                            Regent Park, Harbourfront   
58                            Regent Park, Harbourfront   
59                            Regent Park, Harbourfront   
60                            Regent Park, Harbourfront   
61                            Regent Park, Harbourfront   
62                            Regent Park, Harbourfront   
63                            Regent Park, Harbourfront   
64                            Regent Park, Harbourfront   
65                            Regent Park, Harbourfront   
66                            Regent Park, Harbourfront   
67                            R

In [149]:
print(toronto_venues.shape)
toronto_venues.head()

(4882, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods              43.753259              -79.329656   
1    Parkwoods              43.753259              -79.329656   
2    Parkwoods              43.753259              -79.329656   
3    Parkwoods              43.753259              -79.329656   
4    Parkwoods              43.753259              -79.329656   

               Venue  Venue Latitude  Venue Longitude        Venue Category  
0    Allwyn's Bakery       43.759840       -79.324719  Caribbean Restaurant  
1    Brookbanks Park       43.751976       -79.332140                  Park  
2        Tim Hortons       43.760668       -79.326368                  Café  
3  Bruno's valu-mart       43.746143       -79.324630         Grocery Store  
4                A&W       43.760643       -79.326865  Fast Food Restaurant

In [150]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                              49   
Alderwood, Long Branch                                                 26   
Bathurst Manor, Wilson Heights, Downsview North                        31   
Bayview Village                                                        18   
Bedford Park, Lawrence Manor East                                      40   
Berczy Park                                                           100   
Birch Cliff, Cliffside West                                            14   
Brockton, Parkdale Village, Exhibition Place                          100   
CN Tower, King and Spadina, Railway Lands, Harb...                     15   
Caledonia-Fairbanks                                                    22   
Cedarbrae                                                              28   
Central Bay Street                                                    100   
Christie                                                              100   
Church and Wellesley                                                  100   
Clairville, Humberwood, Woodbine Downs, West Hu...                      4   
Clarks Corners, Tam O'Shanter, Sullivan                                40   
Cliffside, Cliffcrest, Scarborough Village West                        12   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                            100   
Davisville North                                                      100   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                       20   
Don Mills North                                                        31   
Don Mills South                                                        47   
Dorset Park, Wexford Heights, Scarborough Town ...                     44   
Downsview Central                                                       4   
Downsview East                                                         20   
Downsview Northwest                                                    34   
Downsview West                                                          8   
Dufferin, Dovercourt Village                                           66   
Enclave of L4W                                                         52   
Enclave of M4L                                                         47   
Enclave of M5E                                                        100   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                     19   
Fairview, Henry Farm, Oriole                                           44   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                               50   
Garden District, Ryerson                                              100   
Glencairn                                                              31   
Golden Mile, Clairlea, Oakridge                                        27   
Guildwood, Morningside, West Hill                                      24   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                         100   
Hillcrest Village                                                      22   
Humber Summit                                                          10   
Humberlea, Emery                                                        7   
Humewood-Cedarvale                                                     30   
India Bazaar, The Beaches West                                         74   
Islington Avenue                                                       12   
Kennedy Park, Ionview, East Birchmount Park                            24   
Kensington Market, Chinatown, Grange Park                             100   
Kingsview Village, St. Phillips, Martin Grove G.

### Let's find out how many unique categories can be curated from all the returned venues

In [151]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 329 uniques categories.


## Analyze each neighbourhood

In [152]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Zoo  ATM  Accessories Store  Afghan Restaurant  Airport  Airport Lounge  \
0    0    0                  0                  0        0               0   
1    0    0                  0                  0        0               0   
2    0    0                  0                  0        0               0   
3    0    0                  0                  0        0               0   
4    0    0                  0                  0        0               0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  Aquarium  \
0                    0             0               0             0         0   
1                    0             0               0             0         0   
2                    0             0               0             0         0   
3                    0             0               0             0         0   
4                    0             0               0             0         0   

   Arcade  Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0       0            0           0                    0                 0   
1       0            0           0                    0                 0   
2       0            0           0                    0                 0   
3       0            0           0                    0                 0   
4       0            0           0                    0                 0   

   Athletics & Sports  Auto Dealership  Auto Garage  Auto Workshop  \
0                   0                0            0              0   
1                   0                0            0              0   
2                   0                0            0              0   
3                   0                0            0              0   
4                   0                0            0              0   

   Automotive Shop  BBQ Joint  Baby Store  Badminton Court  Bagel Shop  \
0                0          0           0                0           0   
1                0          0           0                0           0   
2                0          0           0                0           0   
3                0          0           0                0           0   
4                0          0           0                0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  \
0       0     0    0               0                 0                   0   
1       0     0    0               0                 0                   0   
2       0     0    0               0                 0                   0   
3       0     0    0               0                 0                   0   
4       0     0    0               0                 0                   0   

   Beach  Beach Bar  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0      0          0         0           0                   0          0   
1      0          0         0           0                   0          0   
2      0          0         0           0                   0          0   
3      0          0         0           0                   0          0   
4      0          0         0           0                   0          0   

   Bistro  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0       0          0                 0         0              0   
1       0          0                 0         0              0   
2       0          0                 0         0              0   
3       0          0                 0         0              0   
4       0          0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0       

### And let's examine the new dataframe size.

In [153]:
toronto_onehot.shape

(4882, 329)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category


In [154]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood   Zoo       ATM  \
0                                            Agincourt  0.00  0.000000   
1                               Alderwood, Long Branch  0.00  0.000000   
2      Bathurst Manor, Wilson Heights, Downsview North  0.00  0.000000   
3                                      Bayview Village  0.00  0.000000   
4                    Bedford Park, Lawrence Manor East  0.00  0.000000   
5                                          Berczy Park  0.00  0.000000   
6                          Birch Cliff, Cliffside West  0.00  0.000000   
7         Brockton, Parkdale Village, Exhibition Place  0.00  0.000000   
8    CN Tower, King and Spadina, Railway Lands, Har...  0.00  0.000000   
9                                  Caledonia-Fairbanks  0.00  0.045455   
10                                           Cedarbrae  0.00  0.000000   
11                                  Central Bay Street  0.00  0.000000   
12                                            Christie  0.00  0.000000   
13                                Church and Wellesley  0.00  0.000000   
14   Clairville, Humberwood, Woodbine Downs, West H...  0.00  0.000000   
15             Clarks Corners, Tam O'Shanter, Sullivan  0.00  0.000000   
16     Cliffside, Cliffcrest, Scarborough Village West  0.00  0.000000   
17                      Commerce Court, Victoria Hotel  0.00  0.000000   
18                                          Davisville  0.00  0.000000   
19                                    Davisville North  0.00  0.000000   
20    Del Ray, Mount Dennis, Keelsdale and Silverthorn  0.00  0.000000   
21                                     Don Mills North  0.00  0.000000   
22                                     Don Mills South  0.00  0.000000   
23   Dorset Park, Wexford Heights, Scarborough Town...  0.00  0.000000   
24                                   Downsview Central  0.00  0.000000   
25                                      Downsview East  0.00  0.000000   
26                                 Downsview Northwest  0.00  0.000000   
27                                      Downsview West  0.00  0.000000   
28                        Dufferin, Dovercourt Village  0.00  0.000000   
29                                      Enclave of L4W  0.00  0.000000   
30                                      Enclave of M4L  0.00  0.000000   
31                                      Enclave of M5E  0.00  0.000000   
32   Eringate, Bloordale Gardens, Old Burnhamthorpe...  0.00  0.000000   
33                        Fairview, Henry Farm, Oriole  0.00  0.000000   
34              First Canadian Place, Underground city  0.00  0.000000   
35                            Forest Hill North & West  0.00  0.000000   
36                            Garden District, Ryerson  0.00  0.000000   
37                                           Glencairn  0.00  0.000000   
38                     Golden Mile, Clairlea, Oakridge  0.00  0.000000   
39                   Guildwood, Morningside, West Hill  0.00  0.000000   
40   Harbourfront East, Union Station, Toronto Islands  0.00  0.000000   
41                       High Park, The Junction South  0.00  0.000000   
42                                   Hillcrest Village  0.00  0.000000   
43                                       Humber Summit  0.00  0.000000   
44                                    Humberlea, Emery  0.00  0.000000   
45                                  Humewood-Cedarvale  0.00  0.000000   
46                      India Bazaar, The Beaches West  0.00  0.000000   
47                                    Islington Avenue  0.00  0.000000   
48         Kennedy Park, Ionview, East Birchmount Park  0.00  0.000000   
49           Kensington Market, Chinatown, Grange Park  0.00  0.000000   
50   Kingsview Village, St. Phillips, Martin Grove ...  0.00  0.000000   
51                    Lawrence Manor, Lawrence Heights  0.00  0.000000   
52                                       Lawrence Park  0.00  0.000000   
53                                            

In [155]:
toronto_grouped.shape

(102, 329)

#### Let's print each neighborhood along with the top 5 most common venues



In [156]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                  venue  freq
0    Chinese Restaurant  0.14
1         Shopping Mall  0.08
2  Caribbean Restaurant  0.04
3           Pizza Place  0.04
4                Bakery  0.04


----Alderwood, Long Branch----
               venue  freq
0     Discount Store  0.12
1  Convenience Store  0.08
2        Pizza Place  0.08
3           Pharmacy  0.08
4               Park  0.08


----Bathurst Manor, Wilson Heights, Downsview North----
            venue  freq
0     Pizza Place  0.06
1     Coffee Shop  0.06
2            Park  0.06
3            Bank  0.06
4  Ice Cream Shop  0.03


----Bayview Village----
                 venue  freq
0                 Bank  0.11
1        Grocery Store  0.11
2         Intersection  0.11
3  Japanese Restaurant  0.11
4          Gas Station  0.11


----Bedford Park, Lawrence Manor East----
                  venue  freq
0    Italian Restaurant  0.10
1           Coffee Shop  0.08
2           Pizza Place  0.05
3  Fast Food Restaurant  0.05
4        Sa

               venue  freq
0  Convenience Store  0.07
1        Pizza Place  0.07
2        Coffee Shop  0.07
3      Grocery Store  0.07
4     Soccer Stadium  0.03


----India Bazaar, The Beaches West----
                  venue  freq
0     Indian Restaurant  0.07
1           Coffee Shop  0.05
2                 Beach  0.04
3  Fast Food Restaurant  0.04
4                  Park  0.04


----Islington Avenue----
               venue  freq
0           Pharmacy  0.17
1  Convenience Store  0.08
2               Café  0.08
3       Skating Rink  0.08
4        Golf Course  0.08


----Kennedy Park, Ionview, East Birchmount Park----
                  venue  freq
0           Coffee Shop  0.12
1    Chinese Restaurant  0.12
2         Grocery Store  0.08
3  Fast Food Restaurant  0.08
4           Pizza Place  0.08


----Kensington Market, Chinatown, Grange Park----
                           venue  freq
0                           Café  0.10
1                    Coffee Shop  0.05
2                        

               venue  freq
0           Pharmacy  0.17
1  Convenience Store  0.08
2        Coffee Shop  0.08
3           Bus Line  0.08
4        Supermarket  0.08


----Willowdale, Newtonbrook----
                       venue  freq
0          Korean Restaurant  0.13
1                       Park  0.10
2                       Café  0.10
3  Middle Eastern Restaurant  0.06
4                Pizza Place  0.06


----Woburn----
                  venue  freq
0                  Park  0.22
1           Coffee Shop  0.22
2     Indian Restaurant  0.11
3    Chinese Restaurant  0.11
4  Fast Food Restaurant  0.11


----Woodbine Heights----
            venue  freq
0            Park  0.11
1     Coffee Shop  0.11
2            Café  0.07
3  Sandwich Place  0.07
4     Pizza Place  0.07


----York Mills West----
           venue  freq
0     Restaurant  0.22
1           Park  0.22
2   Tennis Court  0.11
3  Grocery Store  0.06
4    Golf Course  0.06


----York Mills, Silver Hills----
             venue  freq
0 

#### Converting into dataframe

In [157]:
# Function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

### Dataframe to display top 10 venues from each neighbourhood

In [158]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt    Chinese Restaurant   
1                           Alderwood, Long Branch        Discount Store   
2  Bathurst Manor, Wilson Heights, Downsview North           Coffee Shop   
3                                  Bayview Village           Gas Station   
4                Bedford Park, Lawrence Manor East    Italian Restaurant   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Shopping Mall                Bakery           Pizza Place   
1           Pizza Place     Convenience Store              Pharmacy   
2           Pizza Place                  Bank                  Park   
3   Japanese Restaurant          Intersection         Grocery Store   
4           Coffee Shop  Fast Food Restaurant        Sandwich Place   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Restaurant  Caribbean Restaurant    Seafood Restaurant   
1                  Park                 Trail   Moroccan Restaurant   
2         Shopping Mall                 Diner   Fried Chicken Joint   
3                  Bank                  Park    Chinese Restaurant   
4           Pizza Place                  Bank      Sushi Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Sushi Restaurant           Supermarket  Sri Lankan Restaurant  
1          Skating Rink         Shopping Mall           Liquor Store  
2               Dog Run      Sushi Restaurant         Sandwich Place  
3                  Café         Shopping Mall                  Trail  
4          Intersection       Thai Restaurant             Baby Store

## Cluster Neighbourhoods

### Run k-means to cluster neighbourhood into 5 clusters

In [159]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 4, 0, 0, 2, 2, 4, 2, 2, 4], dtype=int32)

### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [160]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df
print(df.shape)
# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!


(103, 5)


PostalCode           Borough                      Neighborhood   Latitude  \
0        M3A        North York                         Parkwoods  43.753259   
1        M4A        North York                  Victoria Village  43.725882   
2        M5A  Downtown Toronto         Regent Park, Harbourfront  43.654260   
3        M6A        North York  Lawrence Manor, Lawrence Heights  43.718518   
4        M7A      Queen's Park     Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0 -79.329656             4.0                  Park               Pharmacy   
1 -79.315572             4.0           Coffee Shop  Portuguese Restaurant   
2 -79.360636             2.0           Coffee Shop                   Café   
3 -79.464763             2.0            Restaurant   Fast Food Restaurant   
4 -79.389494             2.0           Coffee Shop    Japanese Restaurant   

  3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0         Shopping Mall                Bus Stop        Discount Store   
1  Gym / Fitness Center             Pizza Place                  Park   
2            Restaurant                     Pub                  Park   
3        Clothing Store  Furniture / Home Store           Coffee Shop   
4      Sushi Restaurant             Pizza Place                  Park   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0       Laundry Service            Supermarket  Caribbean Restaurant   
1           Men's Store            Golf Course          Intersection   
2               Theater         Breakfast Spot                 Diner   
3      Sushi Restaurant  Vietnamese Restaurant   Fried Chicken Joint   
4    Italian Restaurant        Thai Restaurant      Ramen Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0                  Café         Shop & Service  
1   Sporting Goods Shop           Hockey Arena  
2    Italian Restaurant       Sushi Restaurant  
3          Dessert Shop        Supplement Shop  
4                  Café            Yoga Studio

### Finally, let's visualize the resulting clusters

In [161]:
print(toronto_merged.shape)
toronto_merged.dropna(inplace = True)
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype('int32')
print(toronto_merged.shape)

(103, 16)
(102, 16)


In [162]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
#     print(cluster)
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=10,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Examine Clusters

### Cluster 1

In [163]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels      1st Most Common Venue  \
10        North York               0       Fast Food Restaurant   
16              York               0          Convenience Store   
17         Etobicoke               0                Coffee Shop   
18       Scarborough               0                Pizza Place   
26       Scarborough               0                     Bakery   
28        North York               0                Coffee Shop   
29         East York               0                Coffee Shop   
32       Scarborough               0             Ice Cream Shop   
38       Scarborough               0         Chinese Restaurant   
39        North York               0                Gas Station   
44       Scarborough               0                Coffee Shop   
49        North York               0                Coffee Shop   
56              York               0               Intersection   
60        North York               0                      Hotel   
63              York               0                Coffee Shop   
65       Scarborough               0          Electronics Store   
70         Etobicoke               0                Gas Station   
71       Scarborough               0  Middle Eastern Restaurant   
77         Etobicoke               0                   Pharmacy   
78       Scarborough               0         Chinese Restaurant   
82       Scarborough               0       Fast Food Restaurant   
85       Scarborough               0         Chinese Restaurant   
89         Etobicoke               0              Grocery Store   
90       Scarborough               0         Chinese Restaurant   
91  Downtown Toronto               0                Coffee Shop   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
10           Grocery Store    Italian Restaurant           Coffee Shop   
16             Coffee Shop           Pizza Place         Grocery Store   
17       Fish & Chips Shop          Intersection           Pizza Place   
18    Fast Food Restaurant                  Bank      Greek Restaurant   
26             Gas Station           Coffee Shop                  Bank   
28             Pizza Place                  Bank                  Park   
29       Indian Restaurant         Grocery Store               Brewery   
32           Bowling Alley   Japanese Restaurant          Intersection   
38             Coffee Shop  Fast Food Restaurant         Grocery Store   
39     Japanese Restaurant          Intersection         Grocery Store   
44                Bus Line                Bakery          Intersection   
49       Convenience Store           Gas Station    Chinese Restaurant   
56  Furniture / Home Store     Convenience Store         Grocery Store   
60             Pizza Place         Grocery Store        Discount Store   
63             Pizza Place                  Park               Brewery   
65             Coffee Shop              Pharmacy            Restaurant   
70             Pizza Place        Sandwich Place           Flea Market   
71             Pizza Place         Grocery Store          Burger Joint   
77             Pizza Place          Intersection     Mobile Phone Shop   
78           Shopping Mall                Bakery           Pizza Place   
82             Coffee Shop              Pharmacy     Convenience Store   
85             Pizza Place            Playground                  Park   
89             Pizza Place           Auto Garage   Fried Chicken Joint   
90             Pizza Place              Gym Pool                  Bank   
91                    Park         Grocery Store        Breakfast Spot   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
10             Pizza Place           Gas Station         Metro Station   
16                  Bakery          Tennis Court          Optical Shop   
17      College Rec Center              Pharmacy             Pet Store   
18      Mexican Restaurant         Smoothie Shop 

### Cluster 2

In [164]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
45  North York               1                  Park                  Pool   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
45           Yoga Studio           Event Space             Drugstore   

   6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
45   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   

    9th Most Common Venue 10th Most Common Venue  
45  Entertainment Service            Escape Room

### Cluster 3

In [165]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels   1st Most Common Venue  \
2          Downtown Toronto               2             Coffee Shop   
3                North York               2              Restaurant   
4              Queen's Park               2             Coffee Shop   
6               Scarborough               2             Coffee Shop   
7                North York               2             Coffee Shop   
8                 East York               2             Pizza Place   
9          Downtown Toronto               2             Coffee Shop   
13               North York               2              Restaurant   
15         Downtown Toronto               2             Coffee Shop   
19             East Toronto               2                     Pub   
20         Downtown Toronto               2             Coffee Shop   
23                East York               2     Sporting Goods Shop   
24         Downtown Toronto               2             Coffee Shop   
25         Downtown Toronto               2       Korean Restaurant   
30         Downtown Toronto               2             Coffee Shop   
31             West Toronto               2             Coffee Shop   
33               North York               2             Coffee Shop   
34               North York               2  Furniture / Home Store   
35   East York/East Toronto               2                    Café   
36         Downtown Toronto               2             Coffee Shop   
37             West Toronto               2                    Café   
40               North York               2             Coffee Shop   
41             East Toronto               2        Greek Restaurant   
42         Downtown Toronto               2             Coffee Shop   
43             West Toronto               2                    Café   
47             East Toronto               2       Indian Restaurant   
48         Downtown Toronto               2             Coffee Shop   
52               North York               2       Korean Restaurant   
54             East Toronto               2             Coffee Shop   
55               North York               2      Italian Restaurant   
59               North York               2             Coffee Shop   
61          Central Toronto               2                   Trail   
62          Central Toronto               2        Sushi Restaurant   
64                     York               2           Train Station   
67          Central Toronto               2             Coffee Shop   
68          Central Toronto               2                    Park   
69             West Toronto               2                    Café   
73          Central Toronto               2             Coffee Shop   
74          Central Toronto               2                    Café   
75             West Toronto               2                    Café   
76              Mississauga               2             Coffee Shop   
79          Central Toronto               2      Italian Restaurant   
80         Downtown Toronto               2                    Café   
81             West Toronto               2             Coffee Shop   
83          Central Toronto               2             Coffee Shop   
84         Downtown Toronto               2                    Café   
86          Central Toronto               2             Coffee Shop   
87         Downtown Toronto               2         Harbor / Marina   
92   Downtown Toronto Stn A               2             Coffee Shop   
94      Etobicoke Northwest               2                   Hotel   
96         Downtown Toronto               2                    Café   
97         Downtown Toronto               2             Coffee Shop   
98                Etobicoke               2             Coffee Shop   
99         Downtown Toronto               2             Coffee Shop   
100   East Toronto Business               2                    Park   
102               Etobicoke               2 

### Cluster 4

In [166]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels  1st Most Common Venue 2nd Most Common Venue  \
53  North York               3  Vietnamese Restaurant            Food Truck   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
53        Baseball Field           Yoga Studio           Event Space   

   6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
53             Drugstore   Dumpling Restaurant  Eastern European Restaurant   

   9th Most Common Venue 10th Most Common Venue  
53     Electronics Store  Entertainment Service

### Cluster 5

In [167]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0     North York               4                  Park               Pharmacy   
1     North York               4           Coffee Shop  Portuguese Restaurant   
5      Etobicoke               4              Pharmacy                 Bakery   
11     Etobicoke               4                  Park            Pizza Place   
12   Scarborough               4    Italian Restaurant         Breakfast Spot   
14     East York               4           Coffee Shop                   Park   
21          York               4                  Park            Pizza Place   
22   Scarborough               4           Coffee Shop                   Park   
27    North York               4              Pharmacy                   Park   
46    North York               4                  Park          Shopping Mall   
50    North York               4                Bakery    Arts & Crafts Store   
51   Scarborough               4           Pizza Place         Ice Cream Shop   
57    North York               4                Bakery      Convenience Store   
58   Scarborough               4                  Park                  Diner   
66    North York               4            Restaurant                   Park   
72    North York               4              Pharmacy               Bus Line   
88     Etobicoke               4                  Park            Pizza Place   
93     Etobicoke               4        Discount Store            Pizza Place   
101    Etobicoke               4                  Park          Shopping Mall   

           3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0                  Shopping Mall               Bus Stop        Discount Store   
1           Gym / Fitness Center            Pizza Place                  Park   
5                  Grocery Store             Playground     Convenience Store   
11            Mexican Restaurant             Restaurant     Fish & Chips Shop   
12                    Playground           Burger Joint                  Park   
14                   Pizza Place         Sandwich Place                  Café   
21            Mexican Restaurant               Pharmacy                Bakery   
22             Indian Restaurant     Chinese Restaurant              Pharmacy   
27                   Coffee Shop            Pizza Place     Recreation Center   
46                          Bank            Pizza Place         Grocery Store   
50                          Bank            Pizza Place        Medical Center   
51                         Beach             Restaurant                  Park   
57                   Golf Course            Gas Station        Discount Store   
58                      Gym Pool  General Entertainment       Thai Restaurant   
66                  Tennis Court      French Restaurant           Golf Course   
72   Eastern European Restaurant  Entertainment Service         Grocery Store   
88             Indian Restaurant   Fast Food Restaurant          Skating Rink   
93             Convenience Store               Pharmacy                  Park   
101  Eastern European Restaurant         Ice Cream Shop  Gym / Fitness Center   

    6th Most Common Venue 7th Most Common Venue        8th Most Common Venue  \
0         Laundry Service           Supermarket         Caribbean Restaurant   
1             Men's Store           Golf Course                 Intersection   
5                    Bank         Shopping Mall                         Café   
11          Grocery Store                   Gym               Clothing Store   
12            Yoga Studio   Dumpling Restaurant  Eastern European Restaurant   
14         Ice Cream Shop        Farmers Market                 Skating Rink   
21         Discount Store                  Café                Grocery Store   
22      Mobile Phone Shop  Fast Food Restaurant               Farmers Market   
27          Shopping Mall        Sandwich Place